<a href="https://colab.research.google.com/github/lihiShlomit/DSproject/blob/main/license_plates_project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
# @title Connecting to google drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
# @title Seting directories

import os

project_dir = "/content/drive/MyDrive/project"

video_dir = os.path.join(project_dir, "videos")

frames_dir = os.path.join(project_dir, "frames")

with_boxes_dir = os.path.join(project_dir, "with_boxes")

video3_dir = "/content/drive/MyDrive/project/videos/video3"

os.makedirs(video_dir, exist_ok=True)

os.makedirs(frames_dir, exist_ok=True)

os.makedirs(with_boxes_dir, exist_ok=True)

os.makedirs(video3_dir, exist_ok=True)

video_filename = "video.mp4"
video_path = os.path.join(video3_dir, "video.mp4")

In [ ]:
# @title Needed imports for uploading a video

!pip install -q yt-dlp moviepy

import os
import shutil
from google.colab import files
import yt_dlp
from moviepy.editor import VideoFileClip
from PIL import Image


In [ ]:
# @title Upload a video

uploaded = files.upload()
for filename in uploaded.keys():
    shutil.move(filename, video_path)
print(f"Video uploaded to: {video_path}")


Saving cars_dideo_2.mp4 to cars_dideo_2 (3).mp4
Video uploaded to: /content/drive/MyDrive/project/videos/video3/video.mp4


In [4]:
# @title Needed imports and setings to extract frames from videos
from moviepy.editor import VideoFileClip
from PIL import Image

clip = VideoFileClip(video_path)
frame_rate = clip.fps #
duration = clip.duration
frame_count = int(duration * frame_rate)
frames_dir = os.path.join(video3_dir, "frames")
os.makedirs(frames_dir, exist_ok=True)

In [ ]:
# @title Extract frames from video

for i in range(frame_count):
    frame_time = i / frame_rate
    frame = clip.get_frame(frame_time)
    frame_path = os.path.join(frames_dir, f"frame_{i:05d}.jpg")
    Image.fromarray(frame).save(frame_path)

print(f"finished extraction")


finished extraction


In [7]:
!pip install -q ultralytics opencv-python

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 15.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 76.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 59.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 41.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 11.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 188.7/188.7 MB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 86.0 MB/s eta 0:00:00


In [8]:
# @title Cloning and installing yolov5

!git clone https://github.com/ultralytics/yolov5.git
%cd yolov5
!pip install -r requirements.txt

Cloning into 'yolov5'...
remote: Enumerating objects: 17521, done.
remote: Counting objects: 100% (24/24), done.
remote: Compressing objects: 100% (24/24), done.
remote: Total 17521 (delta 9), reused 0 (delta 0), pack-reused 17497 (from 4)
Receiving objects: 100% (17521/17521), 16.62 MiB | 20.31 MiB/s, done.
Resolving deltas: 100% (12005/12005), done.
/content/yolov5


In [5]:
# @title imports for marking a bounding box
import torch
import os
import cv2
from pathlib import Path

In [9]:
# @title Function that creates bounding boxes around the license plates

def plot_one_box(x, img, color=(128, 128, 128), label=None, line_thickness=4):
    tl = line_thickness or int(round(0.002 * max(img.shape[0:2])))
    x1, y1, x2, y2 = map(int, x)
    cv2.rectangle(img, (x1, y1), (x2, y2), color, thickness=tl, lineType=cv2.LINE_AA)
    if label:
        tf = max(tl - 1, 1)
        font_scale = 0.5
        t_size = cv2.getTextSize(label, 0, fontScale=font_scale, thickness=tf)[0]
        c2 = x1 + t_size[0], y1 - t_size[1] - 3
        cv2.rectangle(img, (x1, y1), c2, color, -1, cv2.LINE_AA)
        cv2.putText(img, label, (x1, y1 - 2), 0, font_scale, [255, 255, 255], thickness=tf, lineType=cv2.LINE_AA)

In [10]:
# @title Imports and setings for Identifying cars with yolov5

frames_with_boxes_dir = os.path.join(video3_dir, "with_boxes")
os.makedirs(frames_with_boxes_dir, exist_ok=True)

model = torch.hub.load('ultralytics/yolov5', 'yolov5s', pretrained=True)

cars_crops_dir = os.path.join(video3_dir, "cars_crops")
os.makedirs(cars_crops_dir, exist_ok=True)

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2025-8-11 Python-3.11.13 torch-2.6.0+cu124 CPU

100%|██████████| 14.1M/14.1M [00:00<00:00, 124MB/s]

Fusing layers... 
YOLOv5s summary: 213 layers, 7225885 parameters, 0 gradients, 16.4 GFLOPs
Adding AutoShape... 


In [ ]:
# @title Identifying cars and creating bounding boxes around them

frames_with_boxes_dir = os.path.join(video3_dir, "with_boxes")
os.makedirs(frames_with_boxes_dir, exist_ok=True)

model = torch.hub.load('ultralytics/yolov5', 'yolov5s', pretrained=True)

cars_crops_dir = os.path.join(video3_dir, "cars_crops")
os.makedirs(cars_crops_dir, exist_ok=True)

count=0
for filename in sorted(os.listdir(frames_dir)):
    if filename.endswith(".jpg"):
        img_path = os.path.join(frames_dir, filename)
        img = cv2.imread(img_path)

        results = model(img)

        car_count = 0
        for *box, conf, cls in results.xyxy[0].tolist():
            cls = int(cls)
            label = results.names[cls]
            if label == "car":
                x1, y1, x2, y2 = map(int, box)
                car_crop = img[y1:y2, x1:x2]
                crop_filename = f"{os.path.splitext(filename)[0]}_car{car_count}.jpg"
                crop_path = os.path.join(cars_crops_dir, crop_filename)
                cv2.imwrite(crop_path, car_crop)

                car_count += 1

        for *box, conf, cls in results.xyxy[0].tolist():
            cls = int(cls)
            label = results.names[cls]
            if label == "car":
                x1, y1, x2, y2 = map(int, box)
                cv2.rectangle(img, (x1, y1), (x2, y2), (0, 255, 0), 2)

        output_path = os.path.join(frames_with_boxes_dir, filename)
        cv2.imwrite(output_path, img)

print(f"all cars marked")

  warnings.warn(

Downloading: "https://github.com/ultralytics/yolov5/zipball/master" to /root/.cache/torch/hub/master.zip


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


YOLOv5 🚀 2025-8-11 Python-3.11.13 torch-2.6.0+cu124 CPU

100%|██████████| 14.1M/14.1M [00:00<00:00, 377MB/s]

Fusing layers... 
YOLOv5s summary: 213 layers, 7225885 parameters, 0 gradients, 16.4 GFLOPs
Adding AutoShape... 
  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with am

all cars marked


In [ ]:
# @title Loading the fine-tuned model, that identifies license plates

lp_model = torch.hub.load('ultralytics/yolov5', 'custom', path='/content/drive/MyDrive/project/license_plates_model.pt')

Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2025-8-11 Python-3.11.13 torch-2.6.0+cu124 CPU

Fusing layers... 
YOLOv5s summary: 157 layers, 7012822 parameters, 7012822 gradients, 15.8 GFLOPs
Adding AutoShape... 


In [12]:
# @title Installations to allow use of OCR

!apt-get install -y tesseract-ocr
!pip install pytesseract

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
tesseract-ocr is already the newest version (4.1.1-2.1build1).
0 upgraded, 0 newly installed, 0 to remove and 35 not upgraded.


In [13]:
# @title Imports for placing bound boxes
import os
import cv2
import pytesseract
import re

license_plates_with_boxes_dir = os.path.join(video3_dir, "license_plates_with_boxes")
os.makedirs(license_plates_with_boxes_dir, exist_ok=True)

video3_frames = os.path.join(video3_dir, "frames")

In [ ]:
# @title Identifing license plates, place bounding boxes around them and around the cars in the origional pictures, and run OCR on them

car_count = 0

for filename in sorted(os.listdir(video3_frames)):
    if filename.endswith(".jpg") or filename.endswith(".png"):
        img_path = os.path.join(video3_frames, filename)
        img = cv2.imread(img_path)

        results = model(img)
        car_count = 0
        for *box, conf, cls in results.xyxy[0].tolist():
            cls = int(cls)
            label = results.names[cls]
            if label == "car":
                x1, y1, x2, y2 = map(int, box)
                car_crop = img[y1:y2, x1:x2]

                lp_results = lp_model(car_crop)

                for *lp_box, lp_conf, lp_cls in lp_results.xyxy[0].tolist():
                    lx1, ly1, lx2, ly2 = map(int, lp_box)
                    license_plate_crop = car_crop[ly1:ly2, lx1:lx2]

                    raw_text = pytesseract.image_to_string(license_plate_crop, config='--psm 7').strip()

                    lp_text = re.sub(r'[^0-9]', '', raw_text).strip()

                    if len(lp_text) > 7 and lp_text.startswith("1"):
                        lp_text = lp_text[1:]

                    abs_lx1 = x1 + lx1
                    abs_ly1 = y1 + ly1
                    abs_lx2 = x1 + lx2
                    abs_ly2 = y1 + ly2

                    cv2.rectangle(img, (abs_lx1, abs_ly1), (abs_lx2, abs_ly2), (0, 255, 255), 2)

                    cv2.putText(img, lp_text, (abs_lx1, abs_ly1 - 10), cv2.FONT_HERSHEY_SIMPLEX,
                                0.8, (0, 255, 255), 2, lineType=cv2.LINE_AA)

                plot_one_box([x1, y1, x2, y2], img, label=label, color=(0, 255, 0), line_thickness=4)

                car_count += 1

        output_path = os.path.join(license_plates_with_boxes_dir, filename)
        cv2.imwrite(output_path, img)

print("All frames processed and saved with license plates and texts.")


  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with amp.autocast(autocast):

  with a

All frames processed and saved with license plates and texts.


In [14]:
# @title Combine frames into a video

from moviepy.editor import VideoFileClip
video_path = os.path.join(video3_dir, video_filename)
clip = VideoFileClip(video_path)

from moviepy.editor import ImageSequenceClip
import os

frames_with_boxes_dir = license_plates_with_boxes_dir

frame_files = sorted([os.path.join(frames_with_boxes_dir, f)
                      for f in os.listdir(frames_with_boxes_dir)
                      if f.endswith(".jpg") or f.endswith(".png")])

fps = clip.fps
video_clip = ImageSequenceClip(frame_files, fps=fps)

output_video_path = os.path.join(video3_dir, "output_with_boxes.mp4")
video_clip.write_videofile(output_video_path, codec="libx264")


Moviepy - Building video /content/drive/MyDrive/project/videos/video3/output_with_boxes.mp4.
Moviepy - Writing video /content/drive/MyDrive/project/videos/video3/output_with_boxes.mp4



Moviepy - Done !
Moviepy - video ready /content/drive/MyDrive/project/videos/video3/output_with_boxes.mp4


In [15]:
from IPython.display import Video, display

display(Video(output_video_path, embed=True, width=640))